# ETL Pipeline Preparation
Follow the instructions below to help you create your ETL pipeline.
### 1. Import libraries and load datasets.
- Import Python libraries
- Load `messages.csv` into a dataframe and inspect the first few lines.
- Load `categories.csv` into a dataframe and inspect the first few lines.

In [10]:
# import libraries
import pandas as pd
import numpy as np 
from sqlalchemy import create_engine

In [11]:
!cd data && ls -la

total 33064
drwxr-xr-x   5 dlee  staff       160 Nov 15 14:13 .
drwxr-xr-x  14 dlee  staff       448 Dec  1 12:53 ..
-rw-r--r--@  1 dlee  staff  11854295 Sep  7  2018 disaster_categories.csv
-rw-r--r--@  1 dlee  staff   5064273 Sep  7  2018 disaster_messages.csv
-rw-r--r--@  1 dlee  staff      1184 Nov 15 14:13 process_data.py


In [12]:
# load messages dataset
messages = pd.read_csv('data/disaster_messages.csv')
messages.head()

id                                            message  \
0   2  Weather update - a cold front from Cuba that c...   
1   7            Is the Hurricane over or is it not over   
2   8                    Looking for someone but no name   
3   9  UN reports Leogane 80-90 destroyed. Only Hospi...   
4  12  says: west side of Haiti, rest of the country ...   

                                            original   genre  
0  Un front froid se retrouve sur Cuba ce matin. ...  direct  
1                 Cyclone nan fini osinon li pa fini  direct  
2  Patnm, di Maryani relem pou li banm nouvel li ...  direct  
3  UN reports Leogane 80-90 destroyed. Only Hospi...  direct  
4  facade ouest d Haiti et le reste du pays aujou...  direct

In [13]:
# load categories dataset
categories = pd.read_csv('data/disaster_categories.csv')
categories.head()

id                                         categories
0   2  related-1;request-0;offer-0;aid_related-0;medi...
1   7  related-1;request-0;offer-0;aid_related-1;medi...
2   8  related-1;request-0;offer-0;aid_related-0;medi...
3   9  related-1;request-1;offer-0;aid_related-1;medi...
4  12  related-1;request-0;offer-0;aid_related-0;medi...

In [14]:
print(messages.info())
print("")
print(categories.info())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 26248 entries, 0 to 26247
Data columns (total 4 columns):
 #   Column    Non-Null Count  Dtype 
---  ------    --------------  ----- 
 0   id        26248 non-null  int64 
 1   message   26248 non-null  object
 2   original  10184 non-null  object
 3   genre     26248 non-null  object
dtypes: int64(1), object(3)
memory usage: 820.4+ KB
None

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 26248 entries, 0 to 26247
Data columns (total 2 columns):
 #   Column      Non-Null Count  Dtype 
---  ------      --------------  ----- 
 0   id          26248 non-null  int64 
 1   categories  26248 non-null  object
dtypes: int64(1), object(1)
memory usage: 410.2+ KB
None


### 2. Merge datasets.
- Merge the messages and categories datasets using the common id
- Assign this combined dataset to `df`, which will be cleaned in the following steps

In [15]:
# merge datasets
df = pd.merge(messages, categories, on='id')
df.head()

id                                            message  \
0   2  Weather update - a cold front from Cuba that c...   
1   7            Is the Hurricane over or is it not over   
2   8                    Looking for someone but no name   
3   9  UN reports Leogane 80-90 destroyed. Only Hospi...   
4  12  says: west side of Haiti, rest of the country ...   

                                            original   genre  \
0  Un front froid se retrouve sur Cuba ce matin. ...  direct   
1                 Cyclone nan fini osinon li pa fini  direct   
2  Patnm, di Maryani relem pou li banm nouvel li ...  direct   
3  UN reports Leogane 80-90 destroyed. Only Hospi...  direct   
4  facade ouest d Haiti et le reste du pays aujou...  direct   

                                          categories  
0  related-1;request-0;offer-0;aid_related-0;medi...  
1  related-1;request-0;offer-0;aid_related-1;medi...  
2  related-1;request-0;offer-0;aid_related-0;medi...  
3  related-1;request-1;offer-0;aid_related-1;medi...  
4  related-1;request-0;offer-0;aid_related-0;medi...

In [16]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 26386 entries, 0 to 26385
Data columns (total 5 columns):
 #   Column      Non-Null Count  Dtype 
---  ------      --------------  ----- 
 0   id          26386 non-null  int64 
 1   message     26386 non-null  object
 2   original    10246 non-null  object
 3   genre       26386 non-null  object
 4   categories  26386 non-null  object
dtypes: int64(1), object(4)
memory usage: 1.2+ MB


### 3. Split `categories` into separate category columns.
- Split the values in the `categories` column on the `;` character so that each value becomes a separate column. You'll find [this method](https://pandas.pydata.org/pandas-docs/version/0.23/generated/pandas.Series.str.split.html) very helpful! Make sure to set `expand=True`.
- Use the first row of categories dataframe to create column names for the categories data.
- Rename columns of `categories` with new column names.

In [17]:
# create a dataframe of the 36 individual category columns
categories = df.categories.str.split(";", expand=True)
categories.head()

0          1        2              3               4   \
0  related-1  request-0  offer-0  aid_related-0  medical_help-0   
1  related-1  request-0  offer-0  aid_related-1  medical_help-0   
2  related-1  request-0  offer-0  aid_related-0  medical_help-0   
3  related-1  request-1  offer-0  aid_related-1  medical_help-0   
4  related-1  request-0  offer-0  aid_related-0  medical_help-0   

                   5                    6           7           8   \
0  medical_products-0  search_and_rescue-0  security-0  military-0   
1  medical_products-0  search_and_rescue-0  security-0  military-0   
2  medical_products-0  search_and_rescue-0  security-0  military-0   
3  medical_products-1  search_and_rescue-0  security-0  military-0   
4  medical_products-0  search_and_rescue-0  security-0  military-0   

              9   ...             26                      27  \
0  child_alone-0  ...  aid_centers-0  other_infrastructure-0   
1  child_alone-0  ...  aid_centers-0  other_infrastructure-0   
2  child_alone-0  ...  aid_centers-0  other_infrastructure-0   
3  child_alone-0  ...  aid_centers-0  other_infrastructure-0   
4  child_alone-0  ...  aid_centers-0  other_infrastructure-0   

                  28        29       30      31            32      33  \
0  weather_related-0  floods-0  storm-0  fire-0  earthquake-0  cold-0   
1  weather_related-1  floods-0  storm-1  fire-0  earthquake-0  cold-0   
2  weather_related-0  floods-0  storm-0  fire-0  earthquake-0  cold-0   
3  weather_related-0  floods-0  storm-0  fire-0  earthquake-0  cold-0   
4  weather_related-0  floods-0  storm-0  fire-0  earthquake-0  cold-0   

                34               35  
0  other_weather-0  direct_report-0  
1  other_weather-0  direct_report-0  
2  other_weather-0  direct_report-0  
3  other_weather-0  direct_report-0  
4  other_weather-0  direct_report-0  

[5 rows x 36 columns]

In [18]:
# select the first row of the categories dataframe
row = categories.iloc[0]

# use this row to extract a list of new column names for categories.
# one way is to apply a lambda function that takes everything 
# up to the second to last character of each string with slicing
category_colnames = [i[0] for i in row.str.split('-')]
print(category_colnames)

['related', 'request', 'offer', 'aid_related', 'medical_help', 'medical_products', 'search_and_rescue', 'security', 'military', 'child_alone', 'water', 'food', 'shelter', 'clothing', 'money', 'missing_people', 'refugees', 'death', 'other_aid', 'infrastructure_related', 'transport', 'buildings', 'electricity', 'tools', 'hospitals', 'shops', 'aid_centers', 'other_infrastructure', 'weather_related', 'floods', 'storm', 'fire', 'earthquake', 'cold', 'other_weather', 'direct_report']


In [19]:
# rename the columns of `categories`
categories.columns = category_colnames
categories.head()

related    request    offer    aid_related    medical_help  \
0  related-1  request-0  offer-0  aid_related-0  medical_help-0   
1  related-1  request-0  offer-0  aid_related-1  medical_help-0   
2  related-1  request-0  offer-0  aid_related-0  medical_help-0   
3  related-1  request-1  offer-0  aid_related-1  medical_help-0   
4  related-1  request-0  offer-0  aid_related-0  medical_help-0   

     medical_products    search_and_rescue    security    military  \
0  medical_products-0  search_and_rescue-0  security-0  military-0   
1  medical_products-0  search_and_rescue-0  security-0  military-0   
2  medical_products-0  search_and_rescue-0  security-0  military-0   
3  medical_products-1  search_and_rescue-0  security-0  military-0   
4  medical_products-0  search_and_rescue-0  security-0  military-0   

     child_alone  ...    aid_centers    other_infrastructure  \
0  child_alone-0  ...  aid_centers-0  other_infrastructure-0   
1  child_alone-0  ...  aid_centers-0  other_infrastructure-0   
2  child_alone-0  ...  aid_centers-0  other_infrastructure-0   
3  child_alone-0  ...  aid_centers-0  other_infrastructure-0   
4  child_alone-0  ...  aid_centers-0  other_infrastructure-0   

     weather_related    floods    storm    fire    earthquake    cold  \
0  weather_related-0  floods-0  storm-0  fire-0  earthquake-0  cold-0   
1  weather_related-1  floods-0  storm-1  fire-0  earthquake-0  cold-0   
2  weather_related-0  floods-0  storm-0  fire-0  earthquake-0  cold-0   
3  weather_related-0  floods-0  storm-0  fire-0  earthquake-0  cold-0   
4  weather_related-0  floods-0  storm-0  fire-0  earthquake-0  cold-0   

     other_weather    direct_report  
0  other_weather-0  direct_report-0  
1  other_weather-0  direct_report-0  
2  other_weather-0  direct_report-0  
3  other_weather-0  direct_report-0  
4  other_weather-0  direct_report-0  

[5 rows x 36 columns]

In [20]:
categories.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 26386 entries, 0 to 26385
Data columns (total 36 columns):
 #   Column                  Non-Null Count  Dtype 
---  ------                  --------------  ----- 
 0   related                 26386 non-null  object
 1   request                 26386 non-null  object
 2   offer                   26386 non-null  object
 3   aid_related             26386 non-null  object
 4   medical_help            26386 non-null  object
 5   medical_products        26386 non-null  object
 6   search_and_rescue       26386 non-null  object
 7   security                26386 non-null  object
 8   military                26386 non-null  object
 9   child_alone             26386 non-null  object
 10  water                   26386 non-null  object
 11  food                    26386 non-null  object
 12  shelter                 26386 non-null  object
 13  clothing                26386 non-null  object
 14  money                   26386 non-null  object
 15  mi

### 4. Convert category values to just numbers 0 or 1.
- Iterate through the category columns in df to keep only the last character of each string (the 1 or 0). For example, `related-0` becomes `0`, `related-1` becomes `1`. Convert the string to a numeric value.
- You can perform [normal string actions on Pandas Series](https://pandas.pydata.org/pandas-docs/stable/text.html#indexing-with-str), like indexing, by including `.str` after the Series. You may need to first convert the Series to be of type string, which you can do with `astype(str)`.

In [21]:
for column in categories:
    # set each value to be the last character of the string
    categories[column] = categories[column].str.split("-").apply(lambda x: x[1])
    
    # convert column from string to numeric
    categories[column] = categories[column].apply(lambda x: int(x))
    
categories.head()

related  request  offer  aid_related  medical_help  medical_products  \
0        1        0      0            0             0                 0   
1        1        0      0            1             0                 0   
2        1        0      0            0             0                 0   
3        1        1      0            1             0                 1   
4        1        0      0            0             0                 0   

   search_and_rescue  security  military  child_alone  ...  aid_centers  \
0                  0         0         0            0  ...            0   
1                  0         0         0            0  ...            0   
2                  0         0         0            0  ...            0   
3                  0         0         0            0  ...            0   
4                  0         0         0            0  ...            0   

   other_infrastructure  weather_related  floods  storm  fire  earthquake  \
0                     0                0       0      0     0           0   
1                     0                1       0      1     0           0   
2                     0                0       0      0     0           0   
3                     0                0       0      0     0           0   
4                     0                0       0      0     0           0   

   cold  other_weather  direct_report  
0     0              0              0  
1     0              0              0  
2     0              0              0  
3     0              0              0  
4     0              0              0  

[5 rows x 36 columns]

### 5. Replace `categories` column in `df` with new category columns.
- Drop the categories column from the df dataframe since it is no longer needed.
- Concatenate df and categories data frames.

In [22]:
# drop the original categories column from `df`
# concatenate the original dataframe with the new `categories` dataframe
df = pd.concat([df, categories], axis=1)
df = df.drop(['categories'], axis=1)
df.head()

id                                            message  \
0   2  Weather update - a cold front from Cuba that c...   
1   7            Is the Hurricane over or is it not over   
2   8                    Looking for someone but no name   
3   9  UN reports Leogane 80-90 destroyed. Only Hospi...   
4  12  says: west side of Haiti, rest of the country ...   

                                            original   genre  related  \
0  Un front froid se retrouve sur Cuba ce matin. ...  direct        1   
1                 Cyclone nan fini osinon li pa fini  direct        1   
2  Patnm, di Maryani relem pou li banm nouvel li ...  direct        1   
3  UN reports Leogane 80-90 destroyed. Only Hospi...  direct        1   
4  facade ouest d Haiti et le reste du pays aujou...  direct        1   

   request  offer  aid_related  medical_help  medical_products  ...  \
0        0      0            0             0                 0  ...   
1        0      0            1             0                 0  ...   
2        0      0            0             0                 0  ...   
3        1      0            1             0                 1  ...   
4        0      0            0             0                 0  ...   

   aid_centers  other_infrastructure  weather_related  floods  storm  fire  \
0            0                     0                0       0      0     0   
1            0                     0                1       0      1     0   
2            0                     0                0       0      0     0   
3            0                     0                0       0      0     0   
4            0                     0                0       0      0     0   

   earthquake  cold  other_weather  direct_report  
0           0     0              0              0  
1           0     0              0              0  
2           0     0              0              0  
3           0     0              0              0  
4           0     0              0              0  

[5 rows x 40 columns]

In [23]:
df.genre.value_counts()

news      13128
direct    10852
social     2406
Name: genre, dtype: int64

In [14]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 26386 entries, 0 to 26385
Data columns (total 40 columns):
 #   Column                  Non-Null Count  Dtype 
---  ------                  --------------  ----- 
 0   id                      26386 non-null  int64 
 1   message                 26386 non-null  object
 2   original                10246 non-null  object
 3   genre                   26386 non-null  object
 4   related                 26386 non-null  int64 
 5   request                 26386 non-null  int64 
 6   offer                   26386 non-null  int64 
 7   aid_related             26386 non-null  int64 
 8   medical_help            26386 non-null  int64 
 9   medical_products        26386 non-null  int64 
 10  search_and_rescue       26386 non-null  int64 
 11  security                26386 non-null  int64 
 12  military                26386 non-null  int64 
 13  child_alone             26386 non-null  int64 
 14  water                   26386 non-null  int64 
 15  fo

### 6. Remove duplicates.
- Check how many duplicates are in this dataset.
- Drop the duplicates.
- Confirm duplicates were removed.

In [15]:
# check number of duplicates
df.duplicated().mean() * df.shape[0]

170.0

In [16]:
df.shape

(26386, 40)

In [17]:
# drop duplicates
df = df[df.duplicated() == False]
df.shape

(26216, 40)

In [18]:
# check number of duplicates
df.duplicated().mean()

0.0

### 7. Save the clean dataset into an sqlite database.
You can do this with pandas [`to_sql` method](https://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.to_sql.html) combined with the SQLAlchemy library. Remember to import SQLAlchemy's `create_engine` in the first cell of this notebook to use it below.

In [ ]:
engine = create_engine('sqlite:///UdacityDisasterResponse.db')
df.to_sql('messages', engine, index=False)

### 8. Use this notebook to complete `etl_pipeline.py`
Use the template file attached in the Resources folder to write a script that runs the steps above to create a database based on new datasets specified by the user. Alternatively, you can complete `etl_pipeline.py` in the classroom on the `Project Workspace IDE` coming later.

In [21]:
print(engine.table_names())

['messages']


In [25]:
mssgs = engine.execute("select * from messages")
for row in mssgs:
    print(row)

(2, 'Weather update - a cold front from Cuba that could pass over Haiti', 'Un front froid se retrouve sur Cuba ce matin. Il pourrait traverser Haiti demain. Des averses de pluie isolee sont encore prevues sur notre region ce soi', 'direct', 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
(7, 'Is the Hurricane over or is it not over', 'Cyclone nan fini osinon li pa fini', 'direct', 1, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0)
(8, 'Looking for someone but no name', 'Patnm, di Maryani relem pou li banm nouvel li ak timoun yo. Mesi se john jean depi Monben kwochi.', 'direct', 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
(9, 'UN reports Leogane 80-90 destroyed. Only Hospital St. Croix functioning. Needs supplies desperately.', 'UN reports Leogane 80-90 destroyed. Only Hospital St. Croix functioning. Needs su

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



(23488, 'The attack comes three days after two grenade blasts in Nairobi which killed one person and wounded dozens of others, to which a Kenyan man has pleaded guilty of involvement.', None, 'news', 1, 0, 0, 1, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
(23490, 'Air force helicopters have been dropping food parcels to the worst hit areas and rescuers also plan to distribute food, vaccines and polyethylene sheets to cyclone victims.', None, 'news', 1, 0, 0, 1, 1, 1, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 1)
(23491, '16 families-Bosniak, Croatian, and Serb-have transformed one hectare of land into garden plots.', None, 'news', 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0)
(23492, 'It was interesting that Jamat -- the militant wing of (the Tehran-backed militant Lebanese group) Hizbollah in Kashmir -- called a ceasefire and hav